# Part 1: Scraping the Data from Wikipedia

### First, I'm making sure all the packages are installed

In [1]:
!pip install bs4
!pip install requests

In [2]:
import pandas as pd
from bs4 import BeautifulSoup
import requests

### Now I'm scraping the table from the wikipedia page

In [3]:
t_url="https://en.wikipedia.org/wiki/List_of_postal_codes_of_Canada:_M"
data=requests.get(t_url).text
table_contents=[]
soup=BeautifulSoup(data,'html5lib')
table=soup.find('table')

### This section makes sure the not assigned boroughs are ignored, and multiple neighborhoods in the same postal code are combined

In [4]:
for row in table.findAll('td'):
    cell={}
    if row.span.text=='Not assigned':
        pass
    else:
        cell['Postalcode']=row.text[:3]
        cell['Borough']=(row.span.text).split('(')[0]
        if( '(' in row.span.text):
            cell['Neighborhood']=(((((row.span.text).split('(')[1]).strip(')')).replace(' /',',')).replace(')',' ')).strip(' ')
            table_contents.append(cell)

### This cell imports the data into a pandas dataframe and cleans a few messy values

In [5]:
df=pd.DataFrame(table_contents)
df['Borough']=df['Borough'].replace({'Downtown TorontoStn A PO Boxes25 the Esplanade':'Downtown Toronto Stn A',
                                    'East TorontoBusiness reply mail Processing Centre969 Eastern':'East Toronto Business',
                                    'EtobicokeNorthwest':'Etobicoke Northwest','East YorkEast Toronto':'East York/East Toronto',
                                    'MississaugaCanada Post Gateway Processing Centre':'Mississauga'})


### Now I'm checking to be sure it loaded correctly

In [6]:
df.head()

Postalcode           Borough                      Neighborhood
0       \nM3        North York                         Parkwoods
1       \nM4        North York                  Victoria Village
2       \nM5  Downtown Toronto         Regent Park, Harbourfront
3       \nM6        North York  Lawrence Manor, Lawrence Heights
4       \nM7      Queen's Park     Ontario Provincial Government

### Getting rid of the weird \n in postal codes

In [7]:
df['Postalcode']=df['Postalcode'].replace('\n','',regex=True)
df.head()

Postalcode           Borough                      Neighborhood
0         M3        North York                         Parkwoods
1         M4        North York                  Victoria Village
2         M5  Downtown Toronto         Regent Park, Harbourfront
3         M6        North York  Lawrence Manor, Lawrence Heights
4         M7      Queen's Park     Ontario Provincial Government

### Finally, checking the shape of the data frame

In [8]:
df.shape

(103, 3)

# Part 2: Geocoding the postal codes

### Import the data from the CSV file

In [9]:
url = "https://cf-courses-data.s3.us.cloud-object-storage.appdomain.cloud/IBMDeveloperSkillsNetwork-DS0701EN-SkillsNetwork/labs_v1/Geospatial_Coordinates.csv"
c = pd.read_csv(url)
c.head()
df2=pd.DataFrame(c)
df2.head()

Postal Code   Latitude  Longitude
0         M1B  43.806686 -79.194353
1         M1C  43.784535 -79.160497
2         M1E  43.763573 -79.188711
3         M1G  43.770992 -79.216917
4         M1H  43.773136 -79.239476

### Merge the data to our current data frame

In [10]:
#rename postal code to match in both data sets & remove trailing spaces to ensure merge
df.columns=['Postal Code','Borough','Neighborhood']
df.head()

df['Postal Code']=df['Postal Code'].str.strip()
df2['Postal Code']=df['Postal Code'].str.strip()

In [11]:
df3=pd.merge(df,df2,how='left',on=['Postal Code'])
df3.head()
#df3.shape()

Postal Code     Borough Neighborhood   Latitude  Longitude
0          M3  North York    Parkwoods  43.806686 -79.194353
1          M3  North York    Parkwoods  43.711112 -79.284577
2          M3  North York    Parkwoods  43.781638 -79.304302
3          M3  North York    Parkwoods  43.754328 -79.442259
4          M3  North York    Parkwoods  43.725882 -79.315572

# Part 3: Cluster and Explore the Neighborhoods

### Import all necessary packages

In [12]:
import numpy as np
import json

!conda install -c conda-forge geopy --yes
from geopy.geocoders import Nominatim

from pandas.io.json import json_normalize

import matplotlib.cm as cm
import matplotlib.colors as colors

from sklearn.cluster import KMeans

!conda install -c conda-forge folium=0.5.0 --yes
import folium

print('Libraries Imported')

Solving environment: ...working... done

# All requested packages already installed.

Solving environment: ...working... done

# All requested packages already installed.

Libraries Imported


### Get the coordinates of Toronto

In [13]:
address='Toronto, CA'

geolocator=Nominatim(user_agent='toronto explorer')
location=geolocator.geocode(address)
latitude=location.latitude
longitude=location.longitude
print('The geographic coordinates of Toronto, Canada are {}, {}'.format(latitude,longitude))

The geographic coordinates of Toronto, Canada are 43.6534817, -79.3839347


### Create a map of Toronto with the neighborhoods on top

In [14]:
maptoronto=folium.Map(location=[latitude,longitude],zoom_start=10)
maptoronto

### Create a new dataframe with Toronto venues

In [25]:
#select only boroughs that contain the name toronto
df4=df3[df3.Borough.str.contains("Toronto",case=False)]
df4.head()
df5=pd.DataFrame(df4)
df5.head()
#df5.shape()

Postal Code           Borough               Neighborhood   Latitude  \
28          M5  Downtown Toronto  Regent Park, Harbourfront  43.763573   
29          M5  Downtown Toronto  Regent Park, Harbourfront  43.692657   
30          M5  Downtown Toronto  Regent Park, Harbourfront  43.799525   
31          M5  Downtown Toronto  Regent Park, Harbourfront  43.757490   
32          M5  Downtown Toronto  Regent Park, Harbourfront  43.782736   

    Longitude  
28 -79.188711  
29 -79.264848  
30 -79.318389  
31 -79.374714  
32 -79.442259

In [26]:
for lat,lng,borough,neighborhood in zip(df5['Latitude'],df5['Longitude'],df5['Borough'],df5['Neighborhood']):
    label='{},{}'.format(neighborhood,borough)
    label=folium.Popup(label,parse_html=True)
    folium.CircleMarker(
    [lat,lng],
    radius=5,
    popup=label,
    color='blue',
    fill=True,
    fill_color='#3186cc',
    fill_opacity=0.7,
    parse_html=False).add_to(maptoronto)
    

In [27]:
maptoronto

### Get my foursquare credentials

In [28]:
CLIENT_ID = 'W0RBWOFCXMGYQG4FOEZK4TGBAER3Z4JR34FKBUXJDL0TB1UY' # your Foursquare ID
CLIENT_SECRET = 'X0XT0H2IQZBP5MZZ43ZS1UZJ2FKU124U2ODCXNECD53F3M14' # your Foursquare Secret
VERSION = '20180607' # Foursquare API version
LIMIT = 100 # A default Foursquare API limit value

print('Your credentails:')
print('CLIENT_ID: ' + CLIENT_ID)
print('CLIENT_SECRET:' + CLIENT_SECRET)

Your credentails:
CLIENT_ID: W0RBWOFCXMGYQG4FOEZK4TGBAER3Z4JR34FKBUXJDL0TB1UY
CLIENT_SECRET:X0XT0H2IQZBP5MZZ43ZS1UZJ2FKU124U2ODCXNECD53F3M14


### Exploring neighborhoods in Toronto

In [29]:
def getNearbyVenues(names, latitudes, longitudes, radius=500):
    
    venues_list=[]
    for name, lat, lng in zip(names, latitudes, longitudes):
        print(name)
            
        # create the API request URL
        url = 'https://api.foursquare.com/v2/venues/explore?&client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}'.format(CLIENT_ID, CLIENT_SECRET, VERSION, lat, lng, radius, LIMIT)
            
        # make the GET request
        results = requests.get(url).json()["response"]['groups'][0]['items']
        
        # return only relevant information for each nearby venue
        venues_list.append([(
            name, 
            lat, 
            lng, 
            v['venue']['name'], 
            v['venue']['location']['lat'], 
            v['venue']['location']['lng'],  
            v['venue']['categories'][0]['name']) for v in results])

    nearby_venues = pd.DataFrame([item for venue_list in venues_list for item in venue_list])
    nearby_venues.columns = ['Neighborhood', 
                  'Neighborhood Latitude', 
                  'Neighborhood Longitude', 
                  'Venue', 
                  'Venue Latitude', 
                  'Venue Longitude', 
                  'Venue Category']
    
    return(nearby_venues)

In [30]:
toronotovenues=getNearbyVenues(names=df5['Neighborhood'],
                              latitudes=df5['Latitude'],
                              longitudes=df5['Longitude']                              )
#i'm noticing there are a lot of repeates, and that doesn't seem to be the case in our nyc lab example...

Regent Park, Harbourfront
Regent Park, Harbourfront
Regent Park, Harbourfront
Regent Park, Harbourfront
Regent Park, Harbourfront
Regent Park, Harbourfront
Regent Park, Harbourfront
Regent Park, Harbourfront
Regent Park, Harbourfront
Regent Park, Harbourfront
Regent Park, Harbourfront
Regent Park, Harbourfront
Regent Park, Harbourfront
Regent Park, Harbourfront
Regent Park, Harbourfront
Regent Park, Harbourfront
Regent Park, Harbourfront
Regent Park, Harbourfront
Garden District, Ryerson
Garden District, Ryerson
Garden District, Ryerson
Garden District, Ryerson
Garden District, Ryerson
Garden District, Ryerson
Garden District, Ryerson
Garden District, Ryerson
Garden District, Ryerson
Garden District, Ryerson
Garden District, Ryerson
Garden District, Ryerson
Garden District, Ryerson
Garden District, Ryerson
Garden District, Ryerson
Garden District, Ryerson
Garden District, Ryerson
Garden District, Ryerson
St. James Town
St. James Town
St. James Town
St. James Town
St. James Town
St. Jam

Roselawn
Roselawn
Roselawn
Roselawn
Roselawn
Roselawn
Roselawn
Roselawn
Roselawn
Roselawn
Roselawn
Roselawn
Roselawn
Roselawn
Roselawn
Roselawn
Roselawn
Davisville North
Davisville North
Davisville North
Davisville North
Davisville North
Davisville North
Davisville North
Davisville North
Davisville North
Davisville North
Davisville North
Davisville North
Davisville North
Davisville North
Davisville North
Davisville North
Davisville North
Davisville North
Davisville North
Forest Hill North & West
Forest Hill North & West
Forest Hill North & West
Forest Hill North & West
Forest Hill North & West
Forest Hill North & West
Forest Hill North & West
Forest Hill North & West
Forest Hill North & West
Forest Hill North & West
Forest Hill North & West
Forest Hill North & West
Forest Hill North & West
Forest Hill North & West
Forest Hill North & West
Forest Hill North & West
Forest Hill North & West
Forest Hill North & West
High Park, The Junction South
High Park, The Junction South
High Park, The

Rosedale
Rosedale
Rosedale
Rosedale
Rosedale
Rosedale
Rosedale
Rosedale
Rosedale
Rosedale
Rosedale
Rosedale
Rosedale
Rosedale
Rosedale
Rosedale
Rosedale
Enclave of M5E
Enclave of M5E
Enclave of M5E
Enclave of M5E
Enclave of M5E
Enclave of M5E
Enclave of M5E
Enclave of M5E
Enclave of M5E
Enclave of M5E
Enclave of M5E
Enclave of M5E
Enclave of M5E
Enclave of M5E
Enclave of M5E
Enclave of M5E
Enclave of M5E
Enclave of M5E
St. James Town, Cabbagetown
St. James Town, Cabbagetown
St. James Town, Cabbagetown
St. James Town, Cabbagetown
St. James Town, Cabbagetown
St. James Town, Cabbagetown
St. James Town, Cabbagetown
St. James Town, Cabbagetown
St. James Town, Cabbagetown
St. James Town, Cabbagetown
St. James Town, Cabbagetown
St. James Town, Cabbagetown
St. James Town, Cabbagetown
St. James Town, Cabbagetown
St. James Town, Cabbagetown
St. James Town, Cabbagetown
St. James Town, Cabbagetown
St. James Town, Cabbagetown
St. James Town, Cabbagetown
First Canadian Place, Underground city
First 

### Check the size of the dataframe and how many venues were returned for each neighborhood

In [32]:
print(toronotovenues.shape)
toronotovenues.head()

(12316, 7)


Neighborhood  Neighborhood Latitude  Neighborhood Longitude  \
0  Regent Park, Harbourfront              43.763573              -79.188711   
1  Regent Park, Harbourfront              43.763573              -79.188711   
2  Regent Park, Harbourfront              43.763573              -79.188711   
3  Regent Park, Harbourfront              43.763573              -79.188711   
4  Regent Park, Harbourfront              43.763573              -79.188711   

                   Venue  Venue Latitude  Venue Longitude       Venue Category  
0         RBC Royal Bank       43.766790       -79.191151                 Bank  
1      G & G Electronics       43.765309       -79.191537    Electronics Store  
2             Sail Sushi       43.765951       -79.191275           Restaurant  
3       Big Bite Burrito       43.766299       -79.190720   Mexican Restaurant  
4  Enterprise Rent-A-Car       43.764076       -79.193406  Rental Car Location

In [33]:
toronotovenues.groupby('Neighborhood').count()

Neighborhood Latitude  \
Neighborhood                                                                
Berczy Park                                                           272   
Brockton, Parkdale Village, Exhibition Place                          257   
CN Tower, King and Spadina, Railway Lands, Harb...                    272   
Central Bay Street                                                    272   
Christie                                                              257   
Church and Wellesley                                                  419   
Commerce Court, Victoria Hotel                                        272   
Davisville                                                            419   
Davisville North                                                      419   
Dufferin, Dovercourt Village                                          257   
Enclave of M4L                                                         27   
Enclave of M5E                                                        272   
First Canadian Place, Underground city                                272   
Forest Hill North & West                                              272   
Garden District, Ryerson                                              272   
Harbourfront East, Union Station, Toronto Islands                     272   
High Park, The Junction South                                         257   
India Bazaar, The Beaches West                                        419   
Kensington Market, Chinatown, Grange Park                             272   
Lawrence Park                                                         419   
Little Portugal, Trinity                                              257   
Moore Park, Summerhill East                                           419   
North Toronto West                                                    419   
Parkdale, Roncesvalles                                                257   
Regent Park, Harbourfront                                             272   
Richmond, Adelaide, King                                              272   
Rosedale                                                              419   
Roselawn                                                              272   
Runnymede, Swansea                                                    257   
St. James Town                                                        272   
St. James Town, Cabbagetown                                           419   
Studio District                                                       419   
Summerhill West, Rathnelly, South Hill, Forest ...                    419   
The Annex, North Midtown, Yorkville                                   272   
The Beaches                                                           419   
The Danforth  East                                                    419   
The Danforth West, Riverdale                                          419   
Toronto Dominion Centre, Design Exchange                              272   
University of Toronto, Harbord                                        272   

                                                    Neighborhood Longitude  \
Neighborhood                                                                 
Berczy Park                                                            272   
Brockton, Parkdale Village, Exhibition Place                           257   
CN Tower, King and Spadina, Railway Lands, Harb...                     272   
Central Bay Street                                                     272   
Christie                                                               257   
Church and Wellesley                                                   419   
Commerce Court, Victoria Hotel                                         272   
Davisville                                                             419   
Davisville North                                                       419   
Dufferin, Dovercourt Village        

### How many unique categories are in the returned venues?

In [34]:
print('There are {} unique cateogories.'.format(len(toronotovenues['Venue Category'].unique())))

There are 212 unique cateogories.


### Analyze each neighborhood

In [39]:
# one hot encoding
toronto_onehot = pd.get_dummies(toronotovenues[['Venue Category']], prefix="", prefix_sep="")

# add neighborhood column back to dataframe
toronto_onehot['Neighborhood'] = toronotovenues['Neighborhood'] 

# define a list of column names
cols=toronto_onehot.columns.tolist()

# move the column name to the beginning
cols.insert(0, cols.pop(cols.index('Neighborhood')))

#reorder the columns
toronto_onehot=toronto_onehot.reindex(columns=cols)

toronto_onehot.head()

Neighborhood  Airport  Airport Food Court  Airport Gate  \
0  Regent Park, Harbourfront        0                   0             0   
1  Regent Park, Harbourfront        0                   0             0   
2  Regent Park, Harbourfront        0                   0             0   
3  Regent Park, Harbourfront        0                   0             0   
4  Regent Park, Harbourfront        0                   0             0   

   Airport Lounge  Airport Service  Airport Terminal  American Restaurant  \
0               0                0                 0                    0   
1               0                0                 0                    0   
2               0                0                 0                    0   
3               0                0                 0                    0   
4               0                0                 0                    0   

   Antique Shop  Arepa Restaurant  ...  Tibetan Restaurant  Toy / Game Store  \
0             0                 0  ...                   0                 0   
1             0                 0  ...                   0                 0   
2             0                 0  ...                   0                 0   
3             0                 0  ...                   0                 0   
4             0                 0  ...                   0                 0   

   Trail  Vegetarian / Vegan Restaurant  Video Store  Vietnamese Restaurant  \
0      0                              0            0                      0   
1      0                              0            0                      0   
2      0                              0            0                      0   
3      0                              0            0                      0   
4      0                              0            0                      0   

   Wine Bar  Wings Joint  Women's Store  Yoga Studio  
0         0            0              0            0  
1         0            0              0            0  
2         0            0              0            0  
3         0            0              0            0  
4         0            0              0            0  

[5 rows x 212 columns]

### Group rows by neighborhood and take the mean of each occurence of each category

In [40]:
toronto_grouped=toronto_onehot.groupby('Neighborhood').mean().reset_index()
toronto_grouped

Neighborhood   Airport  \
0                                         Berczy Park  0.007353   
1        Brockton, Parkdale Village, Exhibition Place  0.000000   
2   CN Tower, King and Spadina, Railway Lands, Har...  0.007353   
3                                  Central Bay Street  0.007353   
4                                            Christie  0.000000   
5                                Church and Wellesley  0.000000   
6                      Commerce Court, Victoria Hotel  0.007353   
7                                          Davisville  0.000000   
8                                    Davisville North  0.000000   
9                        Dufferin, Dovercourt Village  0.000000   
10                                     Enclave of M4L  0.000000   
11                                     Enclave of M5E  0.007353   
12             First Canadian Place, Underground city  0.007353   
13                           Forest Hill North & West  0.007353   
14                           Garden District, Ryerson  0.007353   
15  Harbourfront East, Union Station, Toronto Islands  0.007353   
16                      High Park, The Junction South  0.000000   
17                     India Bazaar, The Beaches West  0.000000   
18          Kensington Market, Chinatown, Grange Park  0.007353   
19                                      Lawrence Park  0.000000   
20                           Little Portugal, Trinity  0.000000   
21                        Moore Park, Summerhill East  0.000000   
22                                 North Toronto West  0.000000   
23                             Parkdale, Roncesvalles  0.000000   
24                          Regent Park, Harbourfront  0.007353   
25                           Richmond, Adelaide, King  0.007353   
26                                           Rosedale  0.000000   
27                                           Roselawn  0.007353   
28                                 Runnymede, Swansea  0.000000   
29                                     St. James Town  0.007353   
30                        St. James Town, Cabbagetown  0.000000   
31                                    Studio District  0.000000   
32  Summerhill West, Rathnelly, South Hill, Forest...  0.000000   
33                The Annex, North Midtown, Yorkville  0.007353   
34                                        The Beaches  0.000000   
35                                 The Danforth  East  0.000000   
36                       The Danforth West, Riverdale  0.000000   
37           Toronto Dominion Centre, Design Exchange  0.007353   
38                     University of Toronto, Harbord  0.007353   

    Airport Food Court  Airport Gate  Airport Lounge  Airport Service  \
0             0.003676      0.003676        0.007353         0.011029   
1             0.000000      0.000000        0.000000         0.000000   
2             0.003676      0.003676        0.007353         0.011029   
3             0.003676      0.003676        0.007353         0.011029   
4             0.000000      0.000000        0.000000         0.000000   
5             0.000000      0.000000        0.000000         0.000000   
6             0.003676      0.003676        0.007353         0.011029   
7             0.000000      0.000000        0.000000         0.000000   
8             0.000000      0.000000        0.000000         0.000000   
9             0.000000      0.000000        0.000000         0.000000   
10            0.000000      0.000000        0.000000         0.000000   
11            0.003676      0.003676        0.007353         0.011029   
12            0.003676      0.003676        0.007353         0.011029   
13            0.003676      0.003676        0.007353         0.011029   
14            0.003676      0.003676        0.007353         0.011029   
15            0.003676      0.003676        0.007353         0.011029   
16            0.000000      0.000000        0.000000         0.000000   
17            0.000000      0.000000        0.

### Print each neighborhood along with the top 5 most common venue types

In [41]:
num_top_venues = 5

for hood in toronto_grouped['Neighborhood']:
    print("----"+hood+"----")
    temp = toronto_grouped[toronto_grouped['Neighborhood'] == hood].T.reset_index()
    temp.columns = ['venue','freq']
    temp = temp.iloc[1:]
    temp['freq'] = temp['freq'].astype(float)
    temp = temp.round({'freq': 2})
    print(temp.sort_values('freq', ascending=False).reset_index(drop=True).head(num_top_venues))
    print('\n')

----Berczy Park----
            venue  freq
0     Coffee Shop  0.06
1            Café  0.04
2            Park  0.04
3      Restaurant  0.04
4  Sandwich Place  0.03


----Brockton, Parkdale Village, Exhibition Place----
                venue  freq
0         Coffee Shop  0.09
1                Café  0.04
2                Park  0.04
3          Restaurant  0.03
4  Italian Restaurant  0.03


----CN Tower, King and Spadina, Railway Lands, Harbourfront West, Bathurst Quay, South Niagara, Island airport----
            venue  freq
0     Coffee Shop  0.06
1            Café  0.04
2            Park  0.04
3      Restaurant  0.04
4  Sandwich Place  0.03


----Central Bay Street----
            venue  freq
0     Coffee Shop  0.06
1            Café  0.04
2            Park  0.04
3      Restaurant  0.04
4  Sandwich Place  0.03


----Christie----
                venue  freq
0         Coffee Shop  0.09
1                Café  0.04
2                Park  0.04
3          Restaurant  0.03
4  Italian Restauran

### Put top venue types by neighborhood into a dataframe

In [44]:
def return_most_common_venues(row, num_top_venues):
    row_categories = row.iloc[1:]
    row_categories_sorted = row_categories.sort_values(ascending=False)
    
    return row_categories_sorted.index.values[0:num_top_venues]

In [45]:
num_top_venues = 10

indicators = ['st', 'nd', 'rd']

# create columns according to number of top venues
columns = ['Neighborhood']
for ind in np.arange(num_top_venues):
    try:
        columns.append('{}{} Most Common Venue'.format(ind+1, indicators[ind]))
    except:
        columns.append('{}th Most Common Venue'.format(ind+1))

# create a new dataframe
neighborhoods_venues_sorted = pd.DataFrame(columns=columns)
neighborhoods_venues_sorted['Neighborhood'] = toronto_grouped['Neighborhood']

for ind in np.arange(toronto_grouped.shape[0]):
    neighborhoods_venues_sorted.iloc[ind, 1:] = return_most_common_venues(toronto_grouped.iloc[ind, :], num_top_venues)

neighborhoods_venues_sorted.head()

Neighborhood 1st Most Common Venue  \
0                                        Berczy Park           Coffee Shop   
1       Brockton, Parkdale Village, Exhibition Place           Coffee Shop   
2  CN Tower, King and Spadina, Railway Lands, Har...           Coffee Shop   
3                                 Central Bay Street           Coffee Shop   
4                                           Christie           Coffee Shop   

  2nd Most Common Venue 3rd Most Common Venue 4th Most Common Venue  \
0                  Café                  Park            Restaurant   
1                  Park                  Café         Grocery Store   
2                  Café                  Park            Restaurant   
3                  Café                  Park            Restaurant   
4                  Park                  Café         Grocery Store   

  5th Most Common Venue 6th Most Common Venue 7th Most Common Venue  \
0    Italian Restaurant        Sandwich Place           Pizza Place   
1                Bakery    Italian Restaurant            Restaurant   
2    Italian Restaurant        Sandwich Place           Pizza Place   
3    Italian Restaurant        Sandwich Place           Pizza Place   
4                Bakery    Italian Restaurant            Restaurant   

  8th Most Common Venue 9th Most Common Venue 10th Most Common Venue  
0  Fast Food Restaurant                   Gym                    Pub  
1    Seafood Restaurant          Cocktail Bar                    Pub  
2  Fast Food Restaurant                   Gym                    Pub  
3  Fast Food Restaurant                   Gym                    Pub  
4    Seafood Restaurant          Cocktail Bar                    Pub

## Cluster the neighborhoods

### Run k means to cluster the neighborhoods into 5 clusters

In [49]:
# set number of clusters
kclusters = 4

toronto_grouped_clustering = toronto_grouped.drop('Neighborhood', 1)

# run k-means clustering
kmeans = KMeans(n_clusters=kclusters, random_state=0).fit(toronto_grouped_clustering)

# check cluster labels generated for each row in the dataframe
kmeans.labels_[0:10]

array([0, 2, 0, 0, 2, 1, 0, 1, 1, 2])

### Create a dataframe that includes the clusters plus the top 10 venues for each neighborhood

In [52]:
# add clustering labels
neighborhoods_venues_sorted.insert(0, 'Cluster Labels', kmeans.labels_)

toronto_merged = df5

# merge manhattan_grouped with manhattan_data to add latitude/longitude for each neighborhood
toronto_merged = toronto_merged.join(neighborhoods_venues_sorted.set_index('Neighborhood'), on='Neighborhood')

toronto_merged.head() 

Postal Code           Borough               Neighborhood   Latitude  \
28          M5  Downtown Toronto  Regent Park, Harbourfront  43.763573   
29          M5  Downtown Toronto  Regent Park, Harbourfront  43.692657   
30          M5  Downtown Toronto  Regent Park, Harbourfront  43.799525   
31          M5  Downtown Toronto  Regent Park, Harbourfront  43.757490   
32          M5  Downtown Toronto  Regent Park, Harbourfront  43.782736   

    Longitude  Cluster Labels 1st Most Common Venue 2nd Most Common Venue  \
28 -79.188711               0           Coffee Shop                  Café   
29 -79.264848               0           Coffee Shop                  Café   
30 -79.318389               0           Coffee Shop                  Café   
31 -79.374714               0           Coffee Shop                  Café   
32 -79.442259               0           Coffee Shop                  Café   

   3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
28                  Park            Restaurant    Italian Restaurant   
29                  Park            Restaurant    Italian Restaurant   
30                  Park            Restaurant    Italian Restaurant   
31                  Park            Restaurant    Italian Restaurant   
32                  Park            Restaurant    Italian Restaurant   

   6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
28        Sandwich Place           Pizza Place  Fast Food Restaurant   
29        Sandwich Place           Pizza Place  Fast Food Restaurant   
30        Sandwich Place           Pizza Place  Fast Food Restaurant   
31        Sandwich Place           Pizza Place  Fast Food Restaurant   
32        Sandwich Place           Pizza Place  Fast Food Restaurant   

   9th Most Common Venue 10th Most Common Venue  
28                   Gym                    Pub  
29                   Gym                    Pub  
30                   Gym                    Pub  
31                   Gym                    Pub  
32                   Gym                    Pub

### Visualize the clusters

In [53]:
# create map
map_clusters = folium.Map(location=[latitude, longitude], zoom_start=11)

# set color scheme for the clusters
x = np.arange(kclusters)
ys = [i + x + (i*x)**2 for i in range(kclusters)]
colors_array = cm.rainbow(np.linspace(0, 1, len(ys)))
rainbow = [colors.rgb2hex(i) for i in colors_array]

# add markers to the map
markers_colors = []
for lat, lon, poi, cluster in zip(toronto_merged['Latitude'], toronto_merged['Longitude'], toronto_merged['Neighborhood'], toronto_merged['Cluster Labels']):
    label = folium.Popup(str(poi) + ' Cluster ' + str(cluster), parse_html=True)
    folium.CircleMarker(
        [lat, lon],
        radius=5,
        popup=label,
        color=rainbow[cluster-1],
        fill=True,
        fill_color=rainbow[cluster-1],
        fill_opacity=0.7).add_to(map_clusters)
       
map_clusters

## Examine the Clusters

### Cluster 1

In [55]:
toronto_merged.loc[toronto_merged['Cluster Labels'] == 0, toronto_merged.columns[[1] + list(range(5, toronto_merged.shape[1]))]]

Borough  Cluster Labels 1st Most Common Venue  \
28    Downtown Toronto               0           Coffee Shop   
29    Downtown Toronto               0           Coffee Shop   
30    Downtown Toronto               0           Coffee Shop   
31    Downtown Toronto               0           Coffee Shop   
32    Downtown Toronto               0           Coffee Shop   
...                ...             ...                   ...   
1407  Downtown Toronto               0           Coffee Shop   
1408  Downtown Toronto               0           Coffee Shop   
1409  Downtown Toronto               0           Coffee Shop   
1410  Downtown Toronto               0           Coffee Shop   
1411  Downtown Toronto               0           Coffee Shop   

     2nd Most Common Venue 3rd Most Common Venue 4th Most Common Venue  \
28                    Café                  Park            Restaurant   
29                    Café                  Park            Restaurant   
30                    Café                  Park            Restaurant   
31                    Café                  Park            Restaurant   
32                    Café                  Park            Restaurant   
...                    ...                   ...                   ...   
1407                  Café                  Park            Restaurant   
1408                  Café                  Park            Restaurant   
1409                  Café                  Park            Restaurant   
1410                  Café                  Park            Restaurant   
1411                  Café                  Park            Restaurant   

     5th Most Common Venue 6th Most Common Venue 7th Most Common Venue  \
28      Italian Restaurant        Sandwich Place           Pizza Place   
29      Italian Restaurant        Sandwich Place           Pizza Place   
30      Italian Restaurant        Sandwich Place           Pizza Place   
31      Italian Restaurant        Sandwich Place           Pizza Place   
32      Italian Restaurant        Sandwich Place           Pizza Place   
...                    ...                   ...                   ...   
1407    Italian Restaurant        Sandwich Place           Pizza Place   
1408    Italian Restaurant        Sandwich Place           Pizza Place   
1409    Italian Restaurant        Sandwich Place           Pizza Place   
1410    Italian Restaurant        Sandwich Place           Pizza Place   
1411    Italian Restaurant        Sandwich Place           Pizza Place   

     8th Most Common Venue 9th Most Common Venue 10th Most Common Venue  
28    Fast Food Restaurant                   Gym                    Pub  
29    Fast Food Restaurant                   Gym                    Pub  
30    Fast Food Restaurant                   Gym                    Pub  
31    Fast Food Restaurant                   Gym                    Pub  
32    Fast Food Restaurant                   Gym                    Pub  
...                    ...                   ...                    ...  
1407  Fast Food Restaurant                   Gym                    Pub  
1408  Fast Food Restaurant                   Gym                    Pub  
1409  Fast Food Restaurant                   Gym                    Pub  
1410  Fast Food Restaurant                   Gym                    Pub  
1411  Fast Food Restaurant                   Gym                    Pub  

[306 rows x 12 columns]

### Cluster 2

In [56]:
toronto_merged.loc[toronto_merged['Cluster Labels'] == 1, toronto_merged.columns[[1] + list(range(5, toronto_merged.shape[1]))]]

Borough  Cluster Labels 1st Most Common Venue  \
264       East Toronto               1           Coffee Shop   
265       East Toronto               1           Coffee Shop   
266       East Toronto               1           Coffee Shop   
267       East Toronto               1           Coffee Shop   
268       East Toronto               1           Coffee Shop   
...                ...             ...                   ...   
1431  Downtown Toronto               1           Coffee Shop   
1432  Downtown Toronto               1           Coffee Shop   
1433  Downtown Toronto               1           Coffee Shop   
1434  Downtown Toronto               1           Coffee Shop   
1435  Downtown Toronto               1           Coffee Shop   

     2nd Most Common Venue 3rd Most Common Venue 4th Most Common Venue  \
264                   Café           Pizza Place            Restaurant   
265                   Café           Pizza Place            Restaurant   
266                   Café           Pizza Place            Restaurant   
267                   Café           Pizza Place            Restaurant   
268                   Café           Pizza Place            Restaurant   
...                    ...                   ...                   ...   
1431                  Café           Pizza Place            Restaurant   
1432                  Café           Pizza Place            Restaurant   
1433                  Café           Pizza Place            Restaurant   
1434                  Café           Pizza Place            Restaurant   
1435                  Café           Pizza Place            Restaurant   

     5th Most Common Venue 6th Most Common Venue 7th Most Common Venue  \
264                  Hotel    Italian Restaurant                Bakery   
265                  Hotel    Italian Restaurant                Bakery   
266                  Hotel    Italian Restaurant                Bakery   
267                  Hotel    Italian Restaurant                Bakery   
268                  Hotel    Italian Restaurant                Bakery   
...                    ...                   ...                   ...   
1431                 Hotel    Italian Restaurant                Bakery   
1432                 Hotel    Italian Restaurant                Bakery   
1433                 Hotel    Italian Restaurant                Bakery   
1434                 Hotel    Italian Restaurant                Bakery   
1435                 Hotel    Italian Restaurant                Bakery   

     8th Most Common Venue 9th Most Common Venue 10th Most Common Venue  
264                   Park      Greek Restaurant    Japanese Restaurant  
265                   Park      Greek Restaurant    Japanese Restaurant  
266                   Park      Greek Restaurant    Japanese Restaurant  
267                   Park      Greek Restaurant    Japanese Restaurant  
268                   Park      Greek Restaurant    Japanese Restaurant  
...                    ...                   ...                    ...  
1431                  Park      Greek Restaurant    Japanese Restaurant  
1432                  Park      Greek Restaurant    Japanese Restaurant  
1433                  Park      Greek Restaurant    Japanese Restaurant  
1434                  Park      Greek Restaurant    Japanese Restaurant  
1435                  Park      Greek Restaurant    Japanese Restaurant  

[266 rows x 12 columns]

### Cluster 3

In [57]:
toronto_merged.loc[toronto_merged['Cluster Labels'] == 2, toronto_merged.columns[[1] + list(range(5, toronto_merged.shape[1]))]]

Borough  Cluster Labels 1st Most Common Venue  \
369   Downtown Toronto               2           Coffee Shop   
370   Downtown Toronto               2           Coffee Shop   
371   Downtown Toronto               2           Coffee Shop   
372   Downtown Toronto               2           Coffee Shop   
373   Downtown Toronto               2           Coffee Shop   
...                ...             ...                   ...   
1161      West Toronto               2           Coffee Shop   
1162      West Toronto               2           Coffee Shop   
1163      West Toronto               2           Coffee Shop   
1164      West Toronto               2           Coffee Shop   
1165      West Toronto               2           Coffee Shop   

     2nd Most Common Venue 3rd Most Common Venue 4th Most Common Venue  \
369                   Park                  Café         Grocery Store   
370                   Park                  Café         Grocery Store   
371                   Park                  Café         Grocery Store   
372                   Park                  Café         Grocery Store   
373                   Park                  Café         Grocery Store   
...                    ...                   ...                   ...   
1161                  Park                  Café         Grocery Store   
1162                  Park                  Café         Grocery Store   
1163                  Park                  Café         Grocery Store   
1164                  Park                  Café         Grocery Store   
1165                  Park                  Café         Grocery Store   

     5th Most Common Venue 6th Most Common Venue 7th Most Common Venue  \
369                 Bakery    Italian Restaurant            Restaurant   
370                 Bakery    Italian Restaurant            Restaurant   
371                 Bakery    Italian Restaurant            Restaurant   
372                 Bakery    Italian Restaurant            Restaurant   
373                 Bakery    Italian Restaurant            Restaurant   
...                    ...                   ...                   ...   
1161                Bakery    Italian Restaurant            Restaurant   
1162                Bakery    Italian Restaurant            Restaurant   
1163                Bakery    Italian Restaurant            Restaurant   
1164                Bakery    Italian Restaurant            Restaurant   
1165                Bakery    Italian Restaurant            Restaurant   

     8th Most Common Venue 9th Most Common Venue 10th Most Common Venue  
369     Seafood Restaurant          Cocktail Bar                    Pub  
370     Seafood Restaurant          Cocktail Bar                    Pub  
371     Seafood Restaurant          Cocktail Bar                    Pub  
372     Seafood Restaurant          Cocktail Bar                    Pub  
373     Seafood Restaurant          Cocktail Bar                    Pub  
...                    ...                   ...                    ...  
1161    Seafood Restaurant          Cocktail Bar                    Pub  
1162    Seafood Restaurant          Cocktail Bar                    Pub  
1163    Seafood Restaurant          Cocktail Bar                    Pub  
1164    Seafood Restaurant          Cocktail Bar                    Pub  
1165    Seafood Restaurant          Cocktail Bar                    Pub  

[98 rows x 12 columns]

### Cluster 4

In [58]:
toronto_merged.loc[toronto_merged['Cluster Labels'] == 3, toronto_merged.columns[[1] + list(range(5, toronto_merged.shape[1]))]]

Borough  Cluster Labels 1st Most Common Venue  \
1436  East Toronto Business               3                Bakery   
1437  East Toronto Business               3                Bakery   
1438  East Toronto Business               3                Bakery   

     2nd Most Common Venue 3rd Most Common Venue 4th Most Common Venue  \
1436                  Bank              Pharmacy                  Park   
1437                  Bank              Pharmacy                  Park   
1438                  Bank              Pharmacy                  Park   

     5th Most Common Venue 6th Most Common Venue 7th Most Common Venue  \
1436                  Café                Lounge               Brewery   
1437                  Café                Lounge               Brewery   
1438                  Café                Lounge               Brewery   

     8th Most Common Venue      9th Most Common Venue 10th Most Common Venue  
1436        Sandwich Place  Middle Eastern Restaurant    Fried Chicken Joint  
1437        Sandwich Place  Middle Eastern Restaurant    Fried Chicken Joint  
1438        Sandwich Place  Middle Eastern Restaurant    Fried Chicken Joint